# Installeerime Pyomo, solveri ja impordime teegid

In [ ]:
# Installeerime Pyomo
!pip install -q pyomo

# Installeerime GLPK GNU Linear Programming Kit solveri
!apt-get install -y -qq glpk-utils -q

# Impordime Pyomo
import pyomo.environ as pyo

# Loome lahendaja klassi
solver = pyo.SolverFactory('glpk', executable='/usr/bin/glpsol')

# Tootmise optimeerimise ülesanne

Meil on tehas, kus toodame tooteid X, Y ja Z. 
* Oleme läbi viinud turuanalüüsi ja teame, et: 
    * toodet X suudaksime ühes nädalas müüa 40 ühikut hinnaga 270 €/tk. 
    * toodet Y suudaksime ühes nädalas müüa nii palju kui toota suudame hinnaga 210 €/tk.
    * toodet Z suudaksime ühes nädalas müüa 20 ühikut hinnaga 250 €/tk
* Kulude osas teame, et:    
    * Toote X tootmiseks kulub 100€ ulatuses toorainet, 1 tund vanemspetsialisti tööd ja 2 tundi nooremspetsialisti tööd.
    * Toote Y tootmiseks kulub 90€ ulatuses toorainet, 1 tund vanemspetsialisti tööd ja 1 tund nooremspetsialisti tööd.
    * Toote Z tootmiseks kulub 95€ ulatuses toorainet, 1 tund vanemspetsialisti tööd ja 1.5 tundi nooremspetsialisti tööd.
* Palgad:
    * Vanemspetsialisti töötund maksab 50€/h
    * Nooremspetsialisti töötund maksab 40€/h
* Ressursipiirangud:
    * Toorainet saame kätte nii palju kui tahame.
    * Vanemspetsialist saab nädalas teha maksimaalselt 80 töötundi.
    * Nooremspetsialist saab nädalas teha maksimaalselt 100 töötundi.

Küsimus: Kui palju tooteid X, Y ja Z peaksime me tootma, et maksimeerida oma kasum ning mis on kasumi suuruseks.

NB: Tooted X ja Y on sinu eest optimeerimisülesandesse juba sisestatud. Sinu ülesandeks on lisada info toote Z kohta.

## Määratleme sisendandmed

In [29]:
# Toodete hinnad ja müügipiirangud
x_hind = 270
x_turupiirang = 40 #maksimumkogus, mida saame müüa
y_hind = 210

# Tooraine kulu ühe toote tootmiseks
x_tooraine = 100
y_tooraine = 90

# Tööjõu hinnad ja müügipiirangud
vanemspets_hind = 50
vanemspets_piirang = 80
nooremspets_hind = 40
nooremspets_piirang = 100

## Loome mudeli

In [30]:
# Loome mudeli
mudel = pyo.ConcreteModel()

## Lisame muutujad
Muutujad on need elemendid, mille õiget väärtust tahame leida. Antud juhul on muutujad toodete X ja Y kogused

In [31]:
# Loome muutujad ehk mille väärtust tahame leida
# Lisaks määratleme, et muutujad peavad kuuluma mittenegatiivsete arvude hulka
mudel.x = pyo.Var(domain=pyo.NonNegativeReals)
mudel.y = pyo.Var(domain=pyo.NonNegativeReals)
mudel.z = pyo.Var(domain=pyo.NonNegativeReals)

## Lisame piirangud
Igal optimeerimisülesandel on piirangud, millega me peame arvestama. Antud näites peame me arvestama turunõudluse ja saadaoleva tööjõuressursiga

In [32]:
# toodet x saame maksimaalselt müüa 40 ühikut nädalas
mudel.x_turg = pyo.Constraint(expr = mudel.x <= x_turupiirang)
# toodet z saame maksimaalselt müüa 50 ühikut nädalas


# vanemspetsialisti tööaega on saada 80 tundi
# ja kõigi toodete tootmiseks kulub üks tund vanemspetsialisti tööd
mudel.vanemspetsialist = pyo.Constraint(expr = mudel.x + mudel.y <= vanemspets_piirang)

#nooremspetsialisti tööaega on saada 100 tundi
# toote X tootmiseks kulub 2, toote Y tootmiseks 1, toote Z tootmiseks 1.5 tundi nooremspetsialisti tööd
mudel.nooremspetsialist = pyo.Constraint(expr = 2*mudel.x + mudel.y <= nooremspets_piirang)

## Defineerime eesmärgi
Meie eesmärgiks on maksimeerida kasum. Eesmärgina defineerime kasumifunktsiooni ja anname mudelile märku, et soovime seda maksimeerida `sense=pyo.maximize`

In [ ]:
# Kui palju kasumit saame ühe toote tootmisest
kasum_x = x_hind - x_tooraine - vanemspets_hind - 2*nooremspets_hind
kasum_y = y_hind - y_tooraine - vanemspets_hind - nooremspets_hind 

# Eesmärk
mudel.kasum = pyo.Objective(expr = mudel.x*kasum_x + mudel.y*kasum_y, sense=pyo.maximize)
mudel.kasum.pprint()

## Lahendame ülesande

In [ ]:
# Lahendame ülesande
solver.solve(mudel).write()

## Vaatame tulemusi

In [ ]:
print("Optimaalne tootmisplaan:\n")
print("Toote X kogus = ", mudel.x())
print("Toote Y kogus = ", mudel.y())
print("Toote Z kogus = ", mudel.z())
print("Kasum = ", mudel.kasum())